# Ex 10

In [1]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
from cv02504.util_functions import (
    PiInv,
    Pi,
    hest,
    find_features,
)

np.random.seed(8)  # for reproducibility

In [2]:
# Ex 10.1
# Load images

im1 = cv2.imread("media/w10_im1.jpg")
im2 = cv2.imread("media/w10_im2.jpg")

fig, ax = plt.subplots(1, 2)
ax[0].imshow(cv2.cvtColor(im1, cv2.COLOR_BGR2RGB))
ax[0].set_title("im1")
ax[0].axis("off")
ax[1].imshow(cv2.cvtColor(im2, cv2.COLOR_BGR2RGB))
ax[1].set_title("im2")
ax[1].axis("off")
plt.show()

In [3]:
matches, kp1, kp2 = find_features(im1, im2)

img3 = cv2.drawMatches(
    im1,
    kp1,
    im2,
    kp2,
    matches[:50],
    None,
    flags=cv2.DrawMatchesFlags_NOT_DRAW_SINGLE_POINTS,
)
mpl.rcParams["figure.figsize"] = [15, 10]
plt.imshow(cv2.cvtColor(img3, cv2.COLOR_BGR2RGB))
plt.axis("off")
plt.title("SIFT features")
plt.show()
mpl.rcParams["figure.figsize"] = [8, 6]

In [4]:
def Hest_dist(H, q1, q2):
    """
    Approximate distance of observed points to a homography matrix.

    Args:
        H: Homography matrix
        q1 (np.array): observed point in image 1, shape (N,2)
        q2 (np.array): observed point in image 2, shape (N,2)

    Returns:
        dist_approx (np.array): Approximate distance
    """
    p1 = PiInv(q1)
    p2 = PiInv(q2)
    distances = np.zeros((p1.shape[1], 1))

    # For each pair of points
    for i in range(p1.shape[1]):
        p1i, p2i = p1[:, i], p2[:, i]
        q1i, q2i = q1[:, i], q2[:, i]
        temp1 = (q1i - Pi(H @ p2i)) ** 2
        temp1 = np.sqrt(np.sum(temp1))
        temp2 = (q2i - Pi(np.linalg.inv(H) @ p1i)) ** 2
        temp2 = np.sqrt(np.sum(temp2))
        distances[i] = temp1 + temp2
    return distances

In [5]:
# Initiate SIFT detector
sift = cv2.SIFT_create()

# Find the keypoints and descriptors with SIFT
kp1, des1 = sift.detectAndCompute(im1, None)
kp2, des2 = sift.detectAndCompute(im2, None)

In [6]:
threshold = 3.84 * 3**2  # 34.56


bf = cv2.BFMatcher(crossCheck=True)
matches = bf.match(des1, des2)
matches = sorted(matches, key=lambda x: x.distance)  # ascending

# Extract matched keypoints
im1_pts = np.float32([kp1[m.queryIdx].pt for m in matches])  # (N,2)
im2_pts = np.float32([kp2[m.trainIdx].pt for m in matches])  # (N,2)

# RANSAC
best_consensus = 0
best_inliers = None
best_H = None

# Randomly select 4 points
idx = np.random.choice(len(im1_pts), 4, replace=False)
q1 = im1_pts[idx]
q2 = im2_pts[idx]
print(f"q1.shape: {q1.shape}\nq2:\n{q2}")

# Estimate homography
H = hest(q1.T, q2.T)

# Calculate distance
distances = Hest_dist(H, im1_pts.T, im2_pts.T)
inliers = [
    [im1_pts[idx], im2_pts[idx]]
    for idx, dist in enumerate(distances)
    if dist < threshold
]
inliers = np.array(inliers)  # (M,2,2)
print(f"inliers: {inliers.shape}")
consensus = inliers.shape[0]
print(f"cons: {consensus}")

q1.shape: (4, 2)
q2:
[[491.8977   516.2788  ]
 [583.7414    76.64322 ]
 [295.9956   492.1125  ]
 [580.87805   96.649635]]
inliers: (4, 2, 2)
cons: 4


In [7]:
def ransac_homography(im1, im2, threshold, iters=200, plot=False):
    """
    Estimate homography matrix using RANSAC.

    Args:
        im1 (np.array): Image 1
        im2 (np.array): Image 2
        threshold (float|int): Distance threshold for inliers
        iters (int): Number of iterations
        plot (bool): Visualize inlier matches

    Returns:
        best_H (np.array): Best homography matrix, shape (3,3)
        best_inliers (np.array): Inliers of best homography (M,2,2)
    """

    # Find features
    matches, kp1, kp2 = find_features(im1, im2)

    # Extract matched keypoints
    im1_pts = np.float32([kp1[m.queryIdx].pt for m in matches])  # n x 2
    im2_pts = np.float32([kp2[m.trainIdx].pt for m in matches])

    # RANSAC
    best_consensus = 0
    best_inliers = None
    best_H = None

    for i in range(iters):
        # Randomly select 4 points
        idx = np.random.choice(len(im1_pts), 4, replace=False)
        q1 = im1_pts[idx]
        q2 = im2_pts[idx]

        # Estimate homography
        H = hest(q1.T, q2.T)

        # Calculate distance
        distances = Hest_dist(H, im1_pts.T, im2_pts.T)
        inliers_idx = [
            idx for idx, dist in enumerate(distances) if dist < threshold
        ]
        inliers = np.array(
            [[im1_pts[idx], im2_pts[idx]] for idx in inliers_idx]
        )  # (M,2,2)
        consensus = inliers.shape[0]

        if consensus > best_consensus:
            best_inliers_idx = inliers_idx
            best_inliers = inliers
            best_consensus = consensus
            best_H = H

    if best_H is None:
        raise ValueError("RANSAC did not find any inliers.")

    # Refit homography to inliers
    print(f"Best consensus of {best_consensus} out of {len(im1_pts)} points.")
    best_H = hest(best_inliers[:, 0].T, best_inliers[:, 1].T)

    if plot:
        # Parallel lines should be expected
        plt.imshow(
            cv2.drawMatches(
                im1, kp1, im2, kp2, np.array(matches)[best_inliers_idx], None
            )
        )
        plt.axis("off")
        plt.show()

    return best_H, best_inliers


sigma = 3
threshold = 5.99 * sigma**2
best_H, best_inliers = ransac_homography(im1, im2, threshold, plot=True)
print(f"best_H:\n{best_H}")

In [ ]:
def estimate_homography_ransac(kp1, des1, kp2, des2, iters=200, plot=False):
    """
    Estimate homography matrix using RANSAC.

    Args:
        kp1 (list): Keypoints of image 1
        des1 (np.array): Descriptors of image 1
        kp2 (list): Keypoints of image 2
        des2 (np.array): Descriptors of image 2

    Returns:
        best_H (np.array): Best homography matrix, shape (3,3)
        best_inliers (np.array): Inliers of best homography (M,2,2)
    """

    bf = cv2.BFMatcher(crossCheck=True)
    matches = bf.match(des1, des2)
    matches = sorted(matches, key=lambda x: x.distance)  # ascending

    # Extract matched keypoints
    im1_pts = np.float32([kp1[m.queryIdx].pt for m in matches])  # n x 2
    im2_pts = np.float32([kp2[m.trainIdx].pt for m in matches])

    # RANSAC
    best_consensus = 0
    best_inliers = None
    best_H = None

    for i in range(iters):
        # Randomly select 4 points
        idx = np.random.choice(len(im1_pts), 4, replace=False)
        q1 = im1_pts[idx]
        q2 = im2_pts[idx]

        # Estimate homography
        H = hest(q1.T, q2.T)

        # Calculate distance
        distances = Hest_dist(H, im1_pts.T, im2_pts.T)
        inliers_idx = [
            idx for idx, dist in enumerate(distances) if dist < threshold
        ]
        inliers = np.array(
            [[im1_pts[idx], im2_pts[idx]] for idx in inliers_idx]
        )  # (M,2,2)
        consensus = inliers.shape[0]

        if consensus > best_consensus:
            best_inliers_idx = inliers_idx
            best_inliers = inliers
            best_consensus = consensus
            best_H = H

    if best_H is None:
        raise ValueError("RANSAC did not find any inliers.")

    # Refit homography to inliers
    print(f"Best consensus of {best_consensus} out of {len(im1_pts)} points.")
    best_H = hest(best_inliers[:, 0].T, best_inliers[:, 1].T)

    if plot:
        # Parallel lines should be expected
        plt.imshow(
            cv2.drawMatches(
                im1, kp1, im2, kp2, np.array(matches)[best_inliers_idx], None
            )
        )
        plt.axis("off")
        plt.show()

    return best_H, best_inliers

In [ ]:
def warpImage(im, H, xRange, yRange):
    """
    Warp image, taken from exercise.

    Args:
        im (np.array): Image
        H (np.array): Homography matrix
        xRange (tuple): x-axis range for sampling
        yRange (tuple): y-axis range for sampling

    Returns:
        imWarp (np.array): Warped image, pixel array
        maskWarp (np.array): Warped mask, boolean array
    """
    T = np.eye(3)
    T[:2, 2] = [-xRange[0], -yRange[0]]
    H = T @ H
    outSize = (xRange[1] - xRange[0], yRange[1] - yRange[0])
    mask = np.ones(im.shape[:2], dtype=np.uint8) * 255
    imWarp = cv2.warpPerspective(im, H, outSize)
    maskWarp = cv2.warpPerspective(mask, H, outSize)
    return imWarp, maskWarp

In [ ]:
# xRange and yRange are arbitrarily set for now
xRange = [0, im1.shape[1]]
yRange = [0, im1.shape[0]]

im1_warp, maskWarp = warpImage(im1, best_H, xRange, yRange)
plt.imshow(cv2.cvtColor(im1_warp, cv2.COLOR_BGR2RGB))
plt.axis("off")
plt.title("Warped image of im1")
plt.show()

In [ ]:
# Modify ranges to not lose any pixels
xRange = [-im1.shape[1], im1.shape[1]]
yRange = [int(-0.5 * im1.shape[0]), int(1.5 * im1.shape[0])]

dst_warp_im, dst_warp = warpImage(im2, best_H, xRange, yRange)
src_warp_im, src_warp = warpImage(
    im1, np.eye(3), 2 * xRange, 2 * yRange
)  # reference

fig, ax = plt.subplots(1, 2)
ax[0].imshow(dst_warp, cmap="gray")
ax[0].set_title("dst mask")
ax[0].axis("off")
ax[1].imshow(src_warp, cmap="gray")
ax[1].set_title("src mask")
ax[1].axis("off")
plt.show()

xor = np.logical_xor(dst_warp, src_warp)
non_overlap = np.logical_and(xor, dst_warp)
fig, ax = plt.subplots(1, 2)
ax[0].imshow(xor, cmap="gray")
ax[0].set_title("xor")
ax[0].axis("off")
ax[1].imshow(non_overlap, cmap="gray")
ax[1].set_title("non_overlap")
ax[1].axis("off")
plt.show()

new_dst_img = dst_warp_im.copy()
new_dst_img[non_overlap != 1] = 0
plt.imshow(new_dst_img)
plt.show()

In [ ]:
# Combine the 2 images
combined = new_dst_img + src_warp_im
plt.imshow(cv2.cvtColor(combined, cv2.COLOR_BGR2RGB))
plt.axis("off")
plt.title("Combined images")
plt.show()